In [1]:
import serial
import serial.tools.list_ports
import time
import os
import cv2
import csv
import numpy as np
from datetime import datetime


In [20]:
BAUD_RATE = 9600

In [21]:
def connect():
    # connect to Arduino
    ports = list(serial.tools.list_ports.comports())  # Create a list with info for all devices
    connected = False
    # Look for the word 'Arduino' in device info, store this port
    for p in ports:
        if "Arduino" in p[1]:
            connected = True
            port_arduino = p[0]
            print("Connected to Arduino on port: ", port_arduino)
            break
    if not connected:
        print("No Arduino Found")

    ser = serial.Serial(port_arduino, BAUD_RATE)
    return ser

In [2]:
BAUD_RATE = 9600
ser = serial.Serial('/dev/ttyACM0', BAUD_RATE)

def connect():
    # connect to Arduino
    ports = list(serial.tools.list_ports.comports())  # Create a list with info for all devices
    connected = False
    # Look for the word 'Arduino' in device info, store this port
    for p in ports:
        if "Arduino" in p[1]:
            connected = True
            port_arduino = p[0]
            print("Connected to Arduino on port: ", port_arduino)
            break
    if not connected:
        print("No Arduino Found")

    ser = serial.Serial(port_arduino, BAUD_RATE)
    return ser


def send_cmd(ser,cmd):
    """
    send string command to Arduino

    :param cmd: (string) command to send
    :return:
    """
    # print(cmd)
    for c in cmd:
        # self.ser.write(c.encode())
        ser.write(c.encode())
        time.sleep(.01)
    ser.write('\r'.encode())
    time.sleep(.01)

def clear_buff(ser):
    while ser.in_waiting:
        ser.read()

def read_char(ser):
    # use Serial.print() on Arduino
    c = ser.read().decode()
    return c


In [3]:
ser = connect()

Connected to Arduino on port:  /dev/ttyACM0


In [4]:
clear_buff(ser)
send_cmd(ser, ' ')
ser.write(b' \n') 
clear_buff(ser)

In [5]:
send_cmd(ser, '2 250 0')

In [ ]:
send_cmd(ser, '2 200 350')

In [7]:
import datetime
def get_datetime_str():
    """

    :return: returns current datetime as a string with format yyyy-mm-dd-HH-MM-SS-UUUUUU
    """
    date_time = datetime.datetime.now()
    time_str = str(date_time.time()).split('.') # Get string with just hh:mm:ss
    time_str = time_str[0] + ':'+time_str[1]
    time_str = time_str.replace(':', '-')  # Now hh-mm-ss
    date_str = str(date_time.date())  # Date in format yyyy-mm-dd
    date_time_str = '-'.join([date_str, time_str])
    return date_time_str

In [13]:
get_datetime_str()

'2023-06-26-19-42-18-480889'

In [14]:
print(type(get_datetime_str()))

<class 'str'>


In [21]:
# time1 = get_datetime_str()

In [16]:
# print(time)

2023-06-26-19-43-43-539653


In [8]:
def send_cmd_new(ser, mode, start_x, y_range, cam_int, cam_top):
    count = 0
    while start_x > 0:
        for y in y_range:
            time.sleep(2)
            cmd = f'{mode} {start_x} {y}'
            count += 1
            direction = 'left'
            send_single_cmd(ser, cmd, count, direction, start_x, y, cam_int, cam_top)
            # interior_camprocessor(cam_no_int, count)
            # coordinates(direction, start_x, y, cam_no_top, count)
            # start_x -= 1
            reading = ser.readline().decode()
            if reading != '':
                print(reading)
            # time.sleep(2)

        start_x -= 1

        for y in reversed(y_range):
            cmd = f'{mode} {start_x} {y}'
            count += 1
            direction = 'right'
            send_single_cmd(ser, cmd, count, direction, start_x, y, cam_int, cam_top)
            # interior_camprocessor(cam_no_int, count)
            # coordinates(direction_now, start_x, y, cam_no_top, count)
            # time.sleep(2)

        start_x -= 1

def send_single_cmd(ser, cmd, count, direction, start_x, y, cam_int, cam_top):
    ser.write(cmd.encode())
    ser.write('\r'.encode())
    # time.sleep(0.01)
    # time.sleep(2)
    interior_camprocessor(cam_int, count)
    coordinates(direction, start_x, y, cam_top, count)
    time.sleep(0.01)
    read_char(ser)  


In [9]:

def coordinates(direction_now, x_step_now, y_step_now, cam_no, ith_number):
    camera_matrix = np.array([[682.694, 0, 573.5379], [0, 675.82, 367.535], [0, 0, 1]])
    dist_coeffs = np.array([-0.119, 0.1449, 0.0019, -0.00689, -0.1701])

    aruco_dict = cv2.aruco.getPredefinedDictionary(cv2.aruco.DICT_4X4_50)
    marker_size = 2.6  # or 2.61

        # Function to calculate marker pose
    def estimate_marker_pose(marker_corners):
        rvecs, tvecs, _ = cv2.aruco.estimatePoseSingleMarkers(marker_corners, marker_size, camera_matrix, dist_coeffs)
        return rvecs, tvecs
    cap = cv2.VideoCapture(cam_no)
    with open(output_file, mode='a', newline='') as file:
        writer = csv.writer(file)
        ret, frame = cap.read()  # Capture a single frame
        cap.release()  # Release the capture device

        if ret:
            gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
            corners, ids, _ = cv2.aruco.detectMarkers(gray, aruco_dict)

            if ids is not None:
                rvecs, tvecs = estimate_marker_pose(corners)
                # rvecs, tvecs = cv2.aruco.estimatePoseSingleMarkers(corners, marker_size, camera_matrix, dist_coeffs)
                values = {}
                for i in range(len(ids)):
                    cv2.aruco.drawDetectedMarkers(frame, corners)
                    cv2.aruco.drawAxis(frame, camera_matrix, dist_coeffs, rvecs[i], tvecs[i], marker_size * 0.5)
                    # x, y, z = tvecs[0][0] - tvecs[1][0]
                    if ids[i][0] == 3: # that is the robot wrt top cam
                        variable_name = "var_0"
                        values[variable_name] = tvecs[i][0]
                    elif ids[i][0] == 4:
                        variable_name = "var_1"
                        values[variable_name] = tvecs[i][0]
                    # variable_name = "var_" + str(i)
                    # values[variable_name] = tvecs[i][0]
                    print("Marker ID:", ids[i][0])
                    # print("Position (x, y):", x, y)
                print(values)
                if len(values) == 2:
                    x, y, z = values['var_0'] - values['var_1'] #check obj wrt R is (what minus what)
                else:
                    x = y = z = float("NaN")
                # timestamp = datetime.now().strftime("%Y-%m-%d %H-%M-%S.%f")
                timestamp = get_datetime_str()
                writer.writerow([ith_number, timestamp, x, y, direction_now, x_step_now, y_step_now])
                    # row_data = [ith_number, timestamp, x, y, direction_now, x_step_now, y_step_now]

                    # Open the output file in append mode
                    # with open(output_file, mode='a', newline='') as file:
                    #     writer = csv.writer(file)
                    #     writer.writerow(row_data)

            cv2.imshow("ArUco Marker Detection", frame)
        # cv2.waitKey(0)

    cv2.destroyAllWindows()


In [10]:

def interior_camprocessor(cam_no, ith_number):
    # cap = cv2.VideoCapture(8)
    cap = cv2.VideoCapture(cam_no)
    interval = 0.04  # interval in seconds (25 frames per second)(25Hz)
    counter = 0  # initialize the counter

    # output_folder = "output"

    # Create the output folder if it doesn't exist
    os.makedirs(output_folder, exist_ok=True)

    # while True:
    ret, frame = cap.read()
    if ret:
        # timestamp = datetime.now().strftime("%Y%m%d_%H%M%S.%f")
        timestamp = get_datetime_str()
        filename = os.path.join(output_folder, f"{ith_number}_{timestamp}.jpg")
        cv2.imwrite(filename, frame)
        
        counter += 1  # increment the counter variable
    time.sleep(interval)

    cap.release()
    # break


In [11]:
def cam_ports():
    all_camera_idx_available = []

    for camera_idx in range(30):
        cap = cv2.VideoCapture(camera_idx)
        if cap.isOpened():
            print(f'Camera index available: {camera_idx}')
            all_camera_idx_available.append(camera_idx)
            cap.release()
    print(all_camera_idx_available)

In [11]:
cam_ports()

[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


Camera index available: 0


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src5 reported: Device '/dev/video1' is not a capture device.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
[ WARN:0] global ./modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video1): can't open camera by index
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src6 reported: Internal data stream error.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV

Camera index available: 4
Camera index available: 6


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src11 reported: Device '/dev/video7' is not a capture device.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
[ WARN:0] global ./modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video7): can't open camera by index
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV

...

[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src18 reported: Device '/dev/video14' is not a capture device.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
[ WARN:0] global ./modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video14): can't open camera by index


Camera index available: 15


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src20 reported: Device '/dev/video16' is not a capture device.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
[ WARN:0] global ./modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video16): can't open camera by index
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src21 reported: Cannot identify device '/dev/video17'.
[ WARN:0] global ./modules/videoio/s

[0, 4, 6, 8, 13, 15]


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src32 reported: Cannot identify device '/dev/video28'.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
[ WARN:0] global ./modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video28): can't open camera by index
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (2075) handleMessage OpenCV | GStreamer warning: Embedded video playback halted; module v4l2src33 reported: Cannot identify device '/dev/video29'.
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1053) open OpenCV | GStreamer warning: unable to start pipeline
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (616) isPipelinePlaying

In [12]:
import cv2
from cv2 import aruco
def show_marker():
    # ### Overlay marker ID and video ###
    dict_aruco = aruco.Dictionary_get(aruco.DICT_4X4_50)
    parameters = aruco.DetectorParameters_create()

    cap = cv2.VideoCapture(8)

    try:
        while True:
            ret, frame = cap.read()
            gray = cv2.cvtColor(frame, cv2.COLOR_RGB2GRAY)

            corners, ids, rejectedImgPoints = aruco.detectMarkers(gray, dict_aruco, parameters=parameters)

            frame_markers = aruco.drawDetectedMarkers(frame.copy(), corners, ids)
            cv2.imshow('frame', frame_markers)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
        cv2.destroyWindow('frame')
        cap.release()
    except KeyboardInterrupt:
        cv2.destroyWindow('frame')
        cap.release()


In [24]:
show_marker()

[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


: 

In [21]:
send_cmd(ser, '2 0 0')

In [31]:

reading = ser.readline().decode()

if reading != '':
        print(reading)

6



In [14]:
if __name__ == "__main__":
    mode = '2'
    start_x = 197
    cam_no_int = 8#14
    cam_no_top = 15#6
    y_range = range(0, 350, 10)
    output_file = 'data_collection_new.csv'
    # with open(output_file, mode='w', newline='') as file:
    #     writer = csv.writer(file)
    #     # Updated header row to include direction and x-step columns
    #     writer.writerow(['Serial_no.','Timestamp', 'x_actual', 'y_actual', 'direction', 'x_step', 'y_step'])

    output_folder = "output_images_new"
    send_cmd_new(ser, mode, start_x, y_range, cam_no_int, cam_no_top)

[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


Marker ID: 4
Marker ID: 17
Marker ID: 3
{'var_1': array([ 0.58293577, 24.74415503, 54.68447895]), 'var_0': array([-16.6106776 , -12.31705278,  37.58933442])}




[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


Marker ID: 4
Marker ID: 3
{'var_1': array([ 8.30721489, 24.31032017, 54.64285828]), 'var_0': array([-16.59519693, -12.3339629 ,  37.59100625])}
7



[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


...

[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


Marker ID: 4
Marker ID: 3
{'var_1': array([ 4.48910446, 15.79589531, 54.24231963]), 'var_0': array([-16.81793438, -12.37415757,  37.57209294])}


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1


Marker ID: 4
Marker ID: 3
{'var_1': array([ 5.36625681, 15.40878868, 53.15199057]), 'var_0': array([-16.81793438, -12.37415757,  37.57209294])}


[ WARN:0] global ./modules/videoio/src/cap_gstreamer.cpp (1100) open OpenCV | GStreamer warning: Cannot query video position: status=0, value=-1, duration=-1
